### Example notebook for WorkStation - Differential Gene Expression

This notebook demonstrates reading from API and performing analysis of differential gene expression.
- title: "Differential Gene Expression (DGE)"
- author: "Margaret Paiva"
- author: "Jon Katz"
- date: "19/10/2021"
- output: R notebook

In [17]:
# # Check your R version if packages are not compatible
# R.version

In [4]:
# # Install BiocManager
# if (!requireNamespace("BiocManager", quietly = TRUE))
#     install.packages("BiocManager")

In [3]:
# # Install packages using BiocManager
# for (pkg in c("limma", "fgsea")) {
#     if (!requireNamespace(pkg, quietly = TRUE)) {
#         BiocManager::install(pkg, update = FALSE, ask = FALSE)
#     }
# }

In [31]:
suppressPackageStartupMessages(library(jsonlite))
suppressPackageStartupMessages(library(rjson))
suppressPackageStartupMessages(library(httr))
suppressPackageStartupMessages(library(dplyr))
suppressPackageStartupMessages(library(data.table))
suppressPackageStartupMessages(library(parallel))
suppressPackageStartupMessages(library(limma))
suppressPackageStartupMessages(library(fgsea))
suppressPackageStartupMessages(library(tidyr))
suppressPackageStartupMessages(library(tibble))
suppressPackageStartupMessages(library(ggplot2))
suppressPackageStartupMessages(library(viridis))

Request data from API if it is not done yet.

In [8]:
# # In "gene_list.csv", define a list of genes of interest
# gene_list  <- as.list(read.csv("gene_list.csv")$x)
# gene_list[1:2]

[[1]]
[1] AGR2
400 Levels: A1BG A4GALT ABCA3 ABCC3 ABCG1 ABLIM2 ABLIM3 ACE ACKR3 ACOX2 ... FOXC1

[[2]]
[1] CEACAM6
400 Levels: A1BG A4GALT ABCA3 ABCC3 ABCG1 ABLIM2 ABLIM3 ACE ACKR3 ACOX2 ... FOXC1

In [9]:
# # Define the data to query from API
# data  <- list("request_data_type" = "expression",
#   "request_cancer_type" = c("Renal cell carcinoma", "Prostate", "Adenoid cystic carcinoma", "Breast", 
#                             "Thyroid", "Testicular", "Hepatocellular carcinoma", "Melanoma"),
# #   "request_genes" = c("ATM", "BRCA1", "BRCA2", "BRIP1", "CDK12", "FANCA", "HDAC2", "KRAS", 
# #                       "PALB2", "SRY", "TP53", "NOTCH1", "CCND1", "BARD1", "FBLN2", "CDKN1B", 
# #                       "RB1", "CHEK2", "APOBEC3B", "PALB2"),  # to define a list of genes here
#   "request_genes" = gene_list,  # if a list of genes is defined in a file
#   "request_dataset" = "PDX",
#   "request_key" = "d787ddc1e45f4ac2b68ac43419500515",
#   "request_client" = 99,
#   "request_user" = 99,
#   "request_mode" = 'true') 

In [14]:
# # Request data from API - this may take some time
# request  <-  POST(url = 'https://lumin-fast-api.championsoncology.com/workstation', 
#                   body = data, encode = 'json')
# request
# # A successful request will give "Status: 200"

In [16]:
# # This will save the data file as a .json file in your root directory
# response <- content(request)
# response

In [27]:
# Enter the file name of the .json file in your root directory below
lt  <-  fromJSON(file = "./data/requested_data---19-10-2021---20_44_20.json")

In [28]:
# Create a dataframe from the data
df  <- do.call(rbind, lapply(lt, rbind))
df  <- as.data.frame(df)
df$gene  <- as.character(df$gene)
df$model  <- as.character(df$model)
df$log.tpm  <- as.numeric(df$log.tpm)
head(df, 2)
print(dim(df))

v1       gene_id         log.rsem.rpkm    log.tpm   z                 
1 19463231 ENSG00000005187 2.03154538924124 2.7411490 -0.169317194943646
2 19463234 ENSG00000005243 0.43494348437293 0.7995996 -0.994615041230675
  fold             
1 0.876569685689051
2 0.185174375597962
  trans                                                                                      
1 ENST00000440284:49.26% ENST00000567387:17.78% ENST00000501740:11.52% ENST00000289416:10.09%
2 ENST00000006101:78.76% ENST00000579263:20.8%                                               
  model    sort_key              gene  model_name tumor_type
1 CTG-3501 CTG-3501_Expression_1 ACSM3 CTG-3501   Breast    
2 CTG-3501 CTG-3501_Expression_1 COPZ2 CTG-3501   Breast

[1] 82800    12


In [32]:
# Pivot the data to have 'gene' as rows, 'model' as colomns, and 'log.tpm' as values
# And filter out values close to 0
log_tpm <- df %>% 
    select(c('gene', 'model', 'log.tpm'))  %>% 
    pivot_wider(names_from = model, values_from = log.tpm)  %>% 
    column_to_rownames('gene')
log_tpm  <- log_tpm[complete.cases(log_tpm),]  # remove rows with missing values
log_tpm[1:2, 1:10]
print(dim(log_tpm))

CTG-3501  CTG-0718 CTG-1181 CTG-0437 CTG-1843 CTG-0456 CTG-2768  CTG-1379
ACSM3 2.7411490 3.214430 2.694151 2.082150 5.471633 2.683937 0.7423767 3.333013
COPZ2 0.7995996 4.130462 7.072492 1.603433 5.820096 6.319975 6.3414629 3.313474
      CTG-1471  CTG-0500 
ACSM3 0.0253033 0.3042442
COPZ2 0.0000000 5.1539376

[1] 400 207


In [20]:
load("../data/RData_uncomp_20210714", verbose=TRUE)

Loading objects:
  cnv.db
  lcpm.list
  lrpkm.lst
  mut.db
  pathways.gmt
  pathways_namming
  rna.seq
  rna.seq.heme
  symbols.dt


[1] "cnv.db"           "lcpm.list"        "lrpkm.lst"        "mut.db"          
[5] "pathways.gmt"     "pathways_namming" "rna.seq"          "rna.seq.heme"    
[9] "symbols.dt"

In [23]:
head(cnv.db)

Model    Gene    Alteration
1 CTG-0009 OR4F5   Gain      
2 CTG-0009 IFI6    Loss      
3 CTG-0009 FAM76A  Loss      
4 CTG-0009 STX12   Loss      
5 CTG-0009 PPP1R8  Loss      
6 CTG-0009 THEMIS2 Loss

In [24]:
head(lcpm.list)

$TGDB
$TGDB$lcpm
                  CTG-0009   CTG-0011    CTG-0012    CTG-0017   CTG-0018
ENSG00000000003 5.71960999 4.92279811 5.201649287 6.078662028 6.35307670
ENSG00000000005 1.16247939 0.00000000 2.527202942 3.987016575 0.00000000
ENSG00000000419 4.99890621 5.26562646 5.857943310 5.745122271 6.12459688
ENSG00000000457 4.70530493 4.57455685 4.944221719 5.640511430 4.62305502
ENSG00000000460 3.89763181 3.67171671 4.567840822 5.624798763 4.37495851
ENSG00000000938 2.25294929 0.27817405 0.492766009 0.018576936 0.00000000
ENSG00000000971 6.48749465 7.83409556 0.259442922 0.000000000 0.89043564
ENSG00000001036 5.25554550 7.15192768 5.638644181 4.780612825 6.33154447
ENSG00000001084 6.47716385 4.95305085 5.771680095 6.423547302 5.50062217
ENSG00000001167 5.91657999 5.72578595 5.392669224 6.292169180 6.02267201
ENSG00000001460 3.67697798 4.96168039 3.328283032 4.809736627 4.97375873
ENSG00000001461 6.47014012 6.26014444 5.396628165 6.198577388 8.35480684
ENSG00000001497 5.22960009 4.83744275 4.637026796 5.587263404 5.21222090
ENSG00000001561 3.47165744 5.66547453 4.210543564 4.541810222 5.22899269
ENSG00000001617 4.52188932 3.35754524 4.772498185 2.899325657 6.38285048
ENSG00000001626 2.30484259 6.26397902 0.534806326 0.467981235 4.17468898
ENSG00000001629 7.00134400 6.24811147 6.381066511 6.281748809 7.21072210
ENSG00000001630 5.83913883 7.83272537 5.953831896 6.884630838 7.46069807
ENSG00000001631 5.73384274 5.46585412 5.982053736 5.317051583 5.90884639
ENSG00000002016 4.40264645 3.05043787 3.160935462 5.307952232 2.87690206
ENSG00000002330 3.20774460 5.63020029 3.178193550 4.212120545 4.98816152
ENSG00000002549 6.06258267 7.51384713 5.665758219 5.071013050 5.58704628
ENSG00000002586 4.26256166 6.02315043 3.867994877 5.090489527 5.17080959
ENSG00000002587 4.21040308 6.70199258 1.933594006 0.789960662 3.14744501
ENSG00000002726 0.00000000 6.96823391 0.028872943 0.000000000 0.42119449
ENSG00000002745 0.15426914 0.00000000 0.218751126 0.000000000 0.00000000
ENSG00000002746 0.84746108 0.55337098 0.901687738 0.387250906 0.14605357
ENSG00000002822 2.38477728 5.48215862 4.900810019 4.339706273 4.89491733
ENSG00000002834 6.83420908 9.21069462 7.063942230 7.716352544 8.71810592
ENSG00000002919 4.51674887 5.54730399 3.126834646 3.671351121 5.08873918
ENSG00000002933 2.96647624 5.59386974 5.351011779 0.000000000 0.00000000
ENSG00000003056 6.82491798 7.35926746 6.888118266 5.689447489 6.95881385
ENSG00000003096 5.39113832 2.05327114 2.300613792 3.155717351 0.56113419
ENSG00000003137 3.19468402 0.53095115 5.736682177 2.760513370 0.53903439
ENSG00000003147 5.08473334 6.64284393 4.991021847 5.176747213 6.57376569
ENSG00000003249 2.61300819 4.83424641 3.360997629 6.278180181 6.13450533
ENSG00000003393 5.57171313 5.76282529 5.400786411 5.692927429 5.50704046
ENSG00000003400 2.07328928 5.38018926 1.536665237 1.463478421 1.44138875
ENSG00000003402 7.97702765 7.54677295 6.696985540 7.388613006 7.26008854
ENSG00000003436 3.33301538 7.58389120 2.911473678 2.532396205 3.25147434
ENSG00000003509 4.80139711 2.74440842 4.570064442 4.279938436 3.83711886
ENSG00000003756 8.70013093 5.57254671 7.679854352 6.178892221 6.81915005
ENSG00000003987 0.96878403 0.06728920 1.381330288 0.155073228 0.54917043
ENSG00000003989 1.53353408 0.25572197 2.184787281 3.495057793 0.13979272
ENSG00000004059 6.32086221 7.11541500 6.902926397 6.058675268 7.83216692
ENSG00000004139 4.76581371 5.04656799 1.857411542 2.603588918 1.76934497
ENSG00000004142 5.87442124 6.88069794 5.788981952 5.929326754 6.94541765
ENSG00000004399 3.72400398 5.33334943 6.992713738 4.710524060 2.49108963
ENSG00000004455 6.75430934 7.59206059 6.827570142 7.854685873 6.71291661
ENSG00000004468 2.34404832 0.88440409 0.682454189 0.555783794 0.42450416
ENSG00000004478 5.78800372 7.39484060 6.622106530 8.929746249 7.75765736
ENSG00000004487 7.08790696 6.56364835 7.301379300 8.134600338 5.99838386
ENSG00000004534 8.01614402 4.71693722 6.757249095 5.667557514 6.88295531
ENSG00000004660 2.11521407 1.69476790 3.7

In [25]:
head(lrpkm.lst)

$TGDB
$TGDB$expression
               CTG-0009    CTG-0011   CTG-0012   CTG-0017    CTG-0018
NA           0.59514866 0.892999056 0.00000000 0.13541493 0.000000000
             0.40121222 0.184134602 0.44715375 0.29861269 0.279354195
A1BG         1.63103221 0.324208732 3.02178627 1.13631364 2.782307868
A1CF         0.18271694 1.571708038 0.21133269 0.15865436 0.151072114
A2M          7.28996718 0.637602182 9.27679152 1.65660399 0.000000000
A2ML1        1.20896297 0.728883708 3.22946074 1.84195070 4.655080439
A4GALT       2.18322239 1.819949362 0.99933422 0.52205486 2.437756895
A4GNT        0.00000000 0.763841617 0.40487977 0.02023315 0.020233152
AAAS         4.93203662 4.118280362 4.08302898 3.37235581 4.899560903
AACS         3.79163022 4.714405364 4.60992717 3.00104197 4.333877338
AADAC        0.37382002 4.291570645 0.75792460 0.68243226 4.998120860
AADACL2      0.18787576 0.281655093 0.04788334 0.04788334 0.047883343
AADACL3      0.00000000 0.052181004 0.00000000 0.00000000 0.000000000
AADACL4      0.07450935 0.000000000 0.00000000 0.00000000 0.056441398
AADAT        3.23869952 1.547212462 2.77778406 2.44091722 1.362380741
AAED1        2.38499125 2.657052809 2.53979041 3.01504132 2.436025586
AAGAB        4.11730021 5.607111719 4.88518645 4.41720490 4.308947849
AAK1         2.47503168 1.617149741 1.48395856 1.49233208 1.727134157
AAMDC        4.28672360 4.342721965 2.60138270 3.69470780 5.321059462
AAMP         4.78628186 6.352125122 5.51260083 5.94524311 6.176287223
AAR2         4.11329655 4.529404275 4.61114218 4.30501989 4.283034628
AARD         3.78178709 0.351824010 5.47449030 7.18856219 3.501181653
AARS         5.47543438 6.030996149 6.16861885 6.07147426 5.516623683
AARS2        2.40896236 2.522212064 4.13802843 3.60762840 3.096434211
AARSD1       5.11706003 4.622704869 4.91747533 3.85971349 4.616143793
AASDH        3.02688042 2.601089102 1.83432117 2.65240224 2.463418567
AASDHPPT     4.22392352 3.974060061 3.51159761 4.40988993 2.523620477
AASS         2.94908312 0.969924608 2.88220965 0.67679194 0.650574365
AATF         3.91560146 5.342658559 3.73701049 4.40191690 4.628995641
AATK         0.70773555 2.338832051 0.95214796 0.46493106 2.386506583
ABAT         2.39810096 2.522333821 2.12986125 1.31310409 1.491606781
ABCA1        1.90296391 1.093350162 1.54362077 0.46533279 0.913221522
ABCA10       1.67285054 0.864665749 0.69334638 0.35569964 0.212206191
ABCA12       0.00000000 1.409084060 0.57090236 0.56095262 0.794541270
ABCA13       2.88052535 0.544764921 1.10775763 1.72418751 0.816966358
ABCA2        3.16936225 2.939694370 4.05936742 2.64024501 3.889849097
ABCA3        1.42532937 0.614609629 2.89061874 3.69428500 3.637544904
ABCA4        1.42973271 0.134188255 2.70900022 1.01284800 2.207604036
ABCA5        2.77085467 2.588932076 3.69635413 2.44056925 1.687127743
ABCA6        1.12219312 0.433209691 0.38106623 0.23129804 0.130957417
ABCA7        2.70419910 1.801982080 1.53637441 3.71915223 4.175626710
ABCA8        0.25051335 0.435717976 0.43195171 0.32051780 0.074590596
ABCA9        0.73315901 0.255198622 0.59945972 0.54587019 0.260598279
ABCB1        0.00000000 0.441120194 0.02597722 0.00000000 0.000000000
ABCB10       3.00772114 3.350011493 3.81500921 3.82294853 3.061349900
ABCB11       0.00000000 0.596114453 0.08858084 0.02224529 0.034534145
ABCB4        0.35699253 0.264286208 1.57146984 0.00000000 0.121055506
ABCB5        0.44398952 0.166096180 0.38410868 0.11080857 0.081440842
ABCB6        4.14629826 3.565682281 4.50592405 3.40495942 3.182244474
ABCB7        3.49846396 3.626955648 2.63776183 3.39503057 2.965400024
ABCB8        2.41807076 4.298160055 3.49441043 2.44052664 3.189960233
ABCB9        1.88453511 2.893890543 2.61095437 1.47812973 2.781826537
ABCC1        3.91797601 3.638041446 4.54572383 3.11740584 3.733823105
ABCC10       4.44344707 3.925760937 4.45022921 4.41464855 4.004340279
ABCC11       0.24154506 0.168829849 0.15213532 0.37251485 0.201084596
ABCC12       0.10469443 0.005512000 0.00000000 0.00000000